In [162]:
import pandas as pd
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.stem import WordNetLemmatizer
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import re

In [163]:
stop_words = set(stopwords.words("english"))

PATTERN_S = re.compile("\'s")  # matches `'s` from text  
PATTERN_RN = re.compile("\\r\\n\\b") #matches `\r` and `\n`
PATTERN_PUNC = re.compile(r"[^\w\s]") # matches all non 0-9 A-z whitespace 


def clean_text(text):
    """
    Series of cleaning. String to lower case, remove non words characters and numbers (punctuation, curly brackets etc).
        text (str): input text
    return (str): modified initial text
    """
    text = text.lower()  # lowercase text
    # replace the matched string with ' '
    text = re.sub(PATTERN_S, ' ', text)
    text = re.sub(PATTERN_RN, ' ', text)
    text = re.sub(PATTERN_PUNC, ' ', text)
    return text

def tokenizer(description, stop_words, normalization):
    
    if normalization == 'lemmatize':
        # tokenize and lemmatize text
        lemmatizer = WordNetLemmatizer()
        tokens = [lemmatizer.lemmatize(w) for w in word_tokenize(description)]
        
    elif normalization == 'stem':
        # tokenize and stem text
        stemmer = PorterStemmer()
        tokens = [stemmer.stem(w) for w in word_tokenize(description)]
    
   # remove tokens length of 2 or below and make all lowercase and remove stop words
    tokens = [w.lower() for w in tokens if (w.lower() not in stop_words) and (len(w) > 2) and(w.isalpha())]
    
    return tokens    
    
def process_query(query, normalization):
    stop_words = set(stopwords.words("english"))
    
    return tokenizer(clean_text(query), stop_words, normalization)

In [164]:
# code example taken from https://towardsdatascience.com/build-a-text-recommendation-system-with-python-e8b95d9f251c
def retrieve_top_n(m, max_docs):
    # return the sum on all tokens of cosinus for each sentence
    if len(m.shape) > 1:
        cos_sim = np.mean(m, axis=0) 
    else: 
        cos_sim = m
    index = np.argsort(cos_sim)[::-1] # from highest idx to smallest score \
    mask = np.ones(len(cos_sim))
    mask = np.logical_or(cos_sim[index] != 0, mask) #eliminate 0 cosine distance
    best_index = index[mask][:max_docs]  
    return best_index

In [165]:
class TfidfRecommenderSystem:
    def __init__(self, docs, num_concepts=100, min_df=1, alpha=1.0, beta=0.75, gamma=0.15):
        self.alpha, self.beta, self.gamma = alpha, beta, gamma
        
        # create a doc-term matrix out of our doc collection
        self.vec = TfidfVectorizer()
        doc_term_mat = self.vec.fit_transform([" ".join(docs[doc_id]) for doc_id in docs])
        result = doc_term_mat
        
        self.q_vecs = {}
        
        self.doc_vecs = result # document vectors in a matrix
        
    def retrieve_docs(self, query, max_docs=10, normalization='lemmatize'):
        query = ' '.join(process_query(query, normalization))
        
        if query not in self.q_vecs:
            q_vec = self.vec.transform([query])
            self.q_vecs[query] = q_vec
        
        ret_docs = {}
        
        mat = cosine_similarity(self.q_vecs[query], self.doc_vecs)
        best_index = retrieve_top_n(mat, max_docs=max_docs)
        
        return best_index
    
    def gather_feedback(self, query, max_docs=10, feedback=None, normalization='lemmatize'):
        """
        This function models the interactive relevance feedback loop
        """
        query = ' '.join(process_query(query, normalization))
        # Step 2: Retrieve the required number of docs in reponse to the queries
        ret_docs = self.retrieve_docs(query, max_docs=max_docs)
        
        
        # display docs to user
        # receive feedback from user

        # Step 3: Obtain feedback from the user in the form of precisions at each rank
        user_feedback = feedback
        # map index to user feedback
        idx_dic = {}
        
        for i, doc in enumerate(ret_docs):
            try:
                idx_dic[doc] = user_feedback[i]
            except:
                idx_dic[doc] = 0

        self.q_vecs[query] = np.dot(self.alpha, self.q_vecs[query])
        for key, value in idx_dic.items():
            if value == 1:
                self.q_vecs[query] += np.dot(self.beta, self.doc_vecs[key])
            else:
                self.q_vecs[query] -= np.dot(self.gamma, self.doc_vecs[key])
        self.q_vecs[query][self.q_vecs[query] < 0] = 0

In [166]:
df = pd.read_pickle(r'assets/processed_df.pkl')
docs = dict(zip(df['naics'], df['lemmatized']))

In [167]:
tfidf_model = TfidfRecommenderSystem(docs)

In [168]:
best_index = tfidf_model.retrieve_docs('Home improvement store')

In [169]:
naics_titles = pd.read_excel('assets/6-digit_2017_Codes.xlsx')
naics_titles['naics'] = naics_titles['naics'].astype(str)

In [170]:
df = df.merge(naics_titles, on='naics', how='outer')

In [171]:
df.iloc[best_index][['naics', 'description']]

naics                                        description
578  442299  Bath shops All Other Home Furnishings Stores  ...
629  453998  Architectural supply stores All Other Miscella...
628  453991  Cigar stores Tobacco Stores  This U S  industr...
577  442291  Curtain and drapery stores  packaged Window Tr...
627  453930  Manufactured  mobile  home dealers Manufacture...
625  453910  Feed stores  pet Pet and Pet Supplies Stores  ...
626  453920  Art auctions Art Dealers  This industry compri...
624  453310  Antique dealers  except motor vehicles  Used M...
594  445299  Coffee and tea  i e   packaged  stores All Oth...
581  444110  Home centers  building materials Home Centers ...

In [172]:
relevant_naics = pd.read_pickle('assets/relevant_naics_df.pkl')

In [173]:
relevant_naics.head()

query                                     relevant_naics
0  Home improvement store  [444110, 444120, 444130, 444190, 444210, 44422...
1    Diesel fuel supplier  [424710, 424720, 424110, 424120, 424130, 42421...
2                  Church  [813100, 813110, 813211, 813212, 813219, 81331...
3                    Farm  [115116, 115111, 115112, 115113, 115114, 11511...
4           Seed supplier  [424910, 424920, 424930, 424940, 424950, 42499...

In [174]:
max_docs = 100

In [175]:
df

naics                                        description  \
0     111110  Soybean farming  field and seed production Soy...   
1     111120  Canola farming  field and seed production Oils...   
2     111130  Bean farming  dry  field and seed production D...   
3     111140  Wheat farming  field and seed production Wheat...   
4     111150  Corn farming  except sweet corn   field and se...   
...      ...                                                ...   
1052  926140  Agricultural cooperative extension program adm...   
1053  926150  Alcoholic beverage control boards Regulation  ...   
1054  927110  National Aeronautics and Space Administration ...   
1055  928110  Air Force National Security  This industry com...   
1056  928120  Consulates International Affairs  This industr...   

                                      clean_description  \
0     soybean farming  field and seed production soy...   
1     canola farming  field and seed production oils...   
2     bean farming  dry  field and seed production d...   
3     wheat farming  field and seed production wheat...   
4     corn farming  except sweet corn   field and se...   
...                                                 ...   
1052  agricultural cooperative extension program adm...   
1053  alcoholic beverage control boards regulation  ...   
1054  national aeronautics and space administration ...   
1055  air force national security  this industry com...   
1056  consulates international affairs  this industr...   

                                             lemmatized  \
0     [soybean, farming, field, seed, production, so...   
1     [canola, farming, field, seed, production, oil...   
2     [bean, farming, dry, field, seed, production, ...   
3     [wheat, farming, field, seed, production, whea...   
4     [corn, farming, except, sweet, corn, field, se...   
...                                                 ...   
1052  [agricultural, cooperative, extension, program...   
1053  [alcoholic, beverage, control, board, regulati...   
1054  [national, aeronautics, space, administration,...   
1055  [air, force, national, security, industry, com...   
1056  [consulate, international, affair, industry, c...   

                                                stemmed  \
0     [soybean, farm, field, seed, product, soybean,...   
1     [canola, farm, field, seed, product, oilse, ex...   
2     [bean, farm, dri, field, seed, product, dri, p...   
3     [wheat, farm, field, seed, product, wheat, far...   
4     [corn, farm, except, sweet, corn, field, seed,...   
...                                                 ...   
1052  [agricultur, cooper, extens, program, administ...   
1053  [alcohol, beverag, control, board, regul, lice...   
1054  [nation, aeronaut, space, administr, space, re...   
1055  [air, forc, nation, secur, thi, industri, comp...   
1056  [consul, intern, affair, thi, industri, compri...   

                                                  title Unnamed: 2  
0                                       Soybean Farming        NaN  
1                     Oilseed (except Soybean) Farming         NaN  
2                             Dry Pea and Bean Farming         NaN  
3                                         Wheat Farming        NaN  
4                                         Corn Farming         NaN  
...                                                 ...        ...  
1052  Regulation of Agricultural Marketing and Commo...        NaN  
1053  Regulation, Licensing, and Inspection of Misce...        NaN  
1054                     Space Research and Technology         NaN  
1055                                 National Security         NaN  
1056                             International Affairs         NaN  

[1057 rows x 7 columns]

## Test Results

In [176]:
def calc_pre_rec_at_n(ret_docs, reljudges, n=-1):
    """
    Calculate precision and recall at n for each query in ret_docs
    """
    
    pre_at_n, rec_at_n = {}, {}
    
    for k, v in ret_docs.items():
        if n > -1 and n <= len(ret_docs):
            s1 = set(v[:n])
        else:
            s1 = set(v)
        s2 = reljudges[k]
        precision = len(s1.intersection(s2)) / len(s1)
        recall = len(s1.intersection(s2)) / len(reljudges[k])
        pre_at_n[k] = round(precision, 3)
        rec_at_n[k] = round(recall, 3)
    return pre_at_n, rec_at_n

In [177]:
def calc_avg_pre(ret_docs, reljudges, cutoff=-1):
    """
    Calculate (mean) average precision for each query in ret_docs
    """
    
    avg_pre, mean_avg_pre = {}, None
    for k, v in ret_docs.items():
        total_rel = 0
        total = 0
        avg_prec = 0
        for i, doc in enumerate(v):
            if doc in reljudges[k] and cutoff == -1:
                total_rel += 1
                total += 1
                precision = total_rel/total
            elif doc in reljudges[k] and i+1 <= cutoff:
                total_rel += 1
                total += 1
                precision = total_rel/total
            else:
                total += 1
                precision = 0
            avg_prec += precision

        avg_pre[k] = round(avg_prec/len(reljudges[k]), 3,)
    
    mean_avg_pre = round(sum(avg_pre.values()) / len(avg_pre), 3)
        
    return avg_pre, mean_avg_pre

In [178]:
import math

def calc_NDCG_at_n(ret_docs, reljudges, n=-1, base=2):
    """
    Calculate NDCG at n for each query in ret_docs
    """
    
    ndcg = {}
    
    for k, v in ret_docs.items():
        
        counts = list(reversed([x for x in range(2,len(reljudges[k])+2)]))
        ideals = {reljudges[k][i]: counts[i] for i in range(len(reljudges[k]))}
        
        add_ons = {}
        if len(v) > len(reljudges[k]):
            for i in range(len(v)-len(reljudges[k])):
                add_ons[i] = 1
        ideals.update(add_ons)
        nums = list(map(ideals.get, v))
        
        systems = {}
        for i, doc in enumerate(v):
            if nums[i] == None:
                systems[doc] = 1
            else:
                systems[doc] = nums[i]
                
        ideal_order = {}
        if n != -1:
            for i, (key, value) in enumerate(ideals.items()):
                if i < n:
                    ideal_order[key] = value
        else:
            ideal_order = ideals
        
        add_ons = {}
        
        
        log = 0
        for i, (doc, rank) in enumerate(ideal_order.items()):
            if i >= len(v):
                break
            elif i < base:
                log += rank
            else:
                log += rank/math.log(i+1, base)

                
        system_order = {}
        if n != -1:
            for i, (key, value) in enumerate(systems.items()):
                if i < n:
                    system_order[key] = value
        else:
            system_order = systems
        
        
        
        system_log = 0
        for i, (doc, rank) in enumerate(system_order.items()):
            if i >= len(v):
                break
            elif i < base:
                system_log += rank
            else:
                system_log += rank/math.log(i+1, base)
        system_log / log
        ndcg[k] = round(system_log / log, 3)
        
    
    return ndcg

In [179]:
ret_docs_dic = {}
queries_dic = {}

for query in relevant_naics.iterrows():
    query_name =  ' '.join(process_query(query[1]['query'], 'lemmatize'))
    ret_docs_index = tfidf_model.retrieve_docs(query_name, max_docs=max_docs)
    ret_docs = df.iloc[ret_docs_index]['naics'].tolist()

    query_docs = query[1]['relevant_naics']
    ret_docs_dic[query_name] = ret_docs
    queries_dic[query_name] = query_docs

In [180]:
ret_docs_dic

{'home improvement store': ['442299',
  '453998',
  '453991',
  '442291',
  '453930',
  '453910',
  '453920',
  '453310',
  '445299',
  '444110',
  '442210',
  '452319',
  '442110',
  '445292',
  '446199',
  '445291',
  '451110',
  '446191',
  '443142',
  '448190',
  '453110',
  '453210',
  '452210',
  '451130',
  '453220',
  '451211',
  '444190',
  '445120',
  '452311',
  '446110',
  '443141',
  '451140',
  '446120',
  '448150',
  '451120',
  '446130',
  '445110',
  '451212',
  '441310',
  '541614',
  '445210',
  '445310',
  '454310',
  '444120',
  '445230',
  '448320',
  '621610',
  '444130',
  '448140',
  '445220',
  '444210',
  '448110',
  '623990',
  '454390',
  '448210',
  '448120',
  '448130',
  '447110',
  '321991',
  '444220',
  '336213',
  '237990',
  '448310',
  '454210',
  '811411',
  '454110',
  '115210',
  '447190',
  '624229',
  '237210',
  '623110',
  '333112',
  '237310',
  '441210',
  '237120',
  '812210',
  '532283',
  '237110',
  '237130',
  '423390',
  '624221',
  

In [181]:
queries_dic

{'home improvement store': ['444110',
  '444120',
  '444130',
  '444190',
  '444210',
  '444220',
  '441110',
  '441120',
  '441210',
  '441222',
  '441228',
  '441310',
  '441320',
  '442110',
  '442210',
  '442291',
  '442299',
  '443141',
  '443142',
  '445110',
  '445120',
  '445210',
  '445220',
  '445230',
  '445291',
  '445292',
  '445299',
  '445310',
  '446110',
  '446120',
  '446130',
  '446191',
  '446199',
  '447110',
  '447190',
  '448110',
  '448120',
  '448130',
  '448140',
  '448150',
  '448190',
  '448210',
  '448310',
  '448320'],
 'diesel fuel supplier': ['424710',
  '424720',
  '424110',
  '424120',
  '424130',
  '424210',
  '424310',
  '424320',
  '424330',
  '424340',
  '424410',
  '424420',
  '424430',
  '424440',
  '424450',
  '424460',
  '424470',
  '424480',
  '424490',
  '424510',
  '424520',
  '424590',
  '424610',
  '424690',
  '424810',
  '424820',
  '424910',
  '424920',
  '424930',
  '424940',
  '424950',
  '424990',
  '423110',
  '423120',
  '423130',
 

In [182]:
calc_pre_rec_at_n(ret_docs_dic, queries_dic, n=-1)[0]

{'home improvement store': 0.39,
 'diesel fuel supplier': 0.07,
 'church': 0.02,
 'farm': 0.64,
 'seed supplier': 0.06,
 'accountant': 0.04,
 'trucking company': 0.06,
 'exporter': 0.01,
 'grain elevator': 0.01,
 'popcorn store': 0.39,
 'agricultural service': 0.15,
 'warehouse': 0.04,
 'agricultural production': 0.64,
 'ranch': 0.64,
 'holding company': 0.03,
 'farm equipment supplier': 0.01,
 'store': 0.18,
 'grocery store': 0.39,
 'rice mill': 0.32,
 'food product supplier': 0.01,
 'accounting firm': 0.37,
 'produce market': 0.03,
 'pet supply store': 0.18,
 'wholesaler': 0.71,
 'produce wholesaler': 0.71,
 'distribution service': 0.46,
 'crop grower': 0.64,
 'addiction treatment center': 0.25,
 'natural good store': 0.24,
 'orchard': 0.64,
 'lumber store': 0.07,
 'mine': 0.28,
 'transportation service': 0.42,
 'investment company': 0.4,
 'fruit wholesaler': 0.71,
 'real estate agency': 0.24,
 'event venue': 0.01,
 'frozen dessert supplier': 0.21,
 'wine wholesaler importer': 0.71,


In [183]:
calc_pre_rec_at_n(ret_docs_dic, queries_dic, n=-1)[1]

{'home improvement store': 0.886,
 'diesel fuel supplier': 0.099,
 'church': 0.04,
 'farm': 1.0,
 'seed supplier': 0.085,
 'accountant': 0.08,
 'trucking company': 0.12,
 'exporter': 0.024,
 'grain elevator': 0.143,
 'popcorn store': 0.886,
 'agricultural service': 0.234,
 'warehouse': 0.571,
 'agricultural production': 1.0,
 'ranch': 1.0,
 'holding company': 1.0,
 'farm equipment supplier': 0.014,
 'store': 0.818,
 'grocery store': 0.886,
 'rice mill': 0.438,
 'food product supplier': 0.014,
 'accounting firm': 0.74,
 'produce market': 0.068,
 'pet supply store': 0.818,
 'wholesaler': 1.0,
 'produce wholesaler': 1.0,
 'distribution service': 0.939,
 'crop grower': 1.0,
 'addiction treatment center': 0.641,
 'natural good store': 0.545,
 'orchard': 1.0,
 'lumber store': 0.099,
 'mine': 1.0,
 'transportation service': 0.84,
 'investment company': 0.976,
 'fruit wholesaler': 1.0,
 'real estate agency': 1.0,
 'event venue': 0.023,
 'frozen dessert supplier': 0.288,
 'wine wholesaler impor

In [184]:
calc_avg_pre(ret_docs_dic, queries_dic, cutoff=5)[0]

{'home improvement store': 0.034,
 'diesel fuel supplier': 0.0,
 'church': 0.02,
 'farm': 0.078,
 'seed supplier': 0.0,
 'accountant': 0.08,
 'trucking company': 0.1,
 'exporter': 0.024,
 'grain elevator': 0.0,
 'popcorn store': 0.045,
 'agricultural service': 0.0,
 'warehouse': 0.205,
 'agricultural production': 0.078,
 'ranch': 0.078,
 'holding company': 1.0,
 'farm equipment supplier': 0.0,
 'store': 0.173,
 'grocery store': 0.032,
 'rice mill': 0.031,
 'food product supplier': 0.0,
 'accounting firm': 0.08,
 'produce market': 0.044,
 'pet supply store': 0.227,
 'wholesaler': 0.07,
 'produce wholesaler': 0.07,
 'distribution service': 0.049,
 'crop grower': 0.078,
 'addiction treatment center': 0.077,
 'natural good store': 0.006,
 'orchard': 0.078,
 'lumber store': 0.0,
 'mine': 0.179,
 'transportation service': 0.1,
 'investment company': 0.051,
 'fruit wholesaler': 0.07,
 'real estate agency': 0.208,
 'event venue': 0.0,
 'frozen dessert supplier': 0.055,
 'wine wholesaler import

In [185]:
calc_avg_pre(ret_docs_dic, queries_dic, cutoff=10)[1]

0.102

In [186]:
calc_NDCG_at_n(ret_docs_dic, queries_dic, n=-1, base=2)

{'home improvement store': 0.596,
 'diesel fuel supplier': 0.089,
 'church': 0.157,
 'farm': 0.926,
 'seed supplier': 0.104,
 'accountant': 0.376,
 'trucking company': 0.457,
 'exporter': 0.186,
 'grain elevator': 0.573,
 'popcorn store': 0.706,
 'agricultural service': 0.235,
 'warehouse': 0.769,
 'agricultural production': 0.895,
 'ranch': 0.9,
 'holding company': 1.0,
 'farm equipment supplier': 0.042,
 'store': 0.655,
 'grocery store': 0.644,
 'rice mill': 0.416,
 'food product supplier': 0.041,
 'accounting firm': 0.664,
 'produce market': 0.302,
 'pet supply store': 0.934,
 'wholesaler': 0.889,
 'produce wholesaler': 0.796,
 'distribution service': 0.595,
 'crop grower': 0.929,
 'addiction treatment center': 0.582,
 'natural good store': 0.398,
 'orchard': 0.899,
 'lumber store': 0.113,
 'mine': 0.96,
 'transportation service': 0.622,
 'investment company': 0.668,
 'fruit wholesaler': 0.868,
 'real estate agency': 0.922,
 'event venue': 0.089,
 'frozen dessert supplier': 0.503,
 

## Stemming

In [187]:
ret_docs_dic = {}
queries_dic = {}

for query in relevant_naics.iterrows():
    query_name =  ' '.join(process_query(query[1]['query'], 'stem'))
    ret_docs_index = tfidf_model.retrieve_docs(query_name, max_docs=max_docs)
    ret_docs = df.iloc[ret_docs_index]['naics'].tolist()

    query_docs = query[1]['relevant_naics']
    ret_docs_dic[query_name] = ret_docs
    queries_dic[query_name] = query_docs

In [188]:
calc_pre_rec_at_n(ret_docs_dic, queries_dic, n=-1)[0]

{'home improv store': 0.39,
 'diesel fuel supplier': 0.07,
 'church': 0.02,
 'farm': 0.64,
 'seed supplier': 0.06,
 'account': 0.0,
 'truck compani': 0.07,
 'export': 0.01,
 'grain elev': 0.01,
 'popcorn store': 0.39,
 'agricultur servic': 0.0,
 'warehous': 0.0,
 'agricultur product': 0.0,
 'ranch': 0.64,
 'hold compani': 0.03,
 'farm equip supplier': 0.21,
 'store': 0.18,
 'groceri store': 0.39,
 'rice mill': 0.32,
 'food product supplier': 0.01,
 'account firm': 0.0,
 'produc market': 0.03,
 'pet suppli store': 0.18,
 'wholesal': 0.01,
 'produc wholesal': 0.01,
 'distribut servic': 0.0,
 'crop grower': 0.64,
 'addict treatment center': 0.24,
 'natur good store': 0.24,
 'orchard': 0.64,
 'lumber store': 0.07,
 'mine': 0.28,
 'transport servic': 0.11,
 'invest compani': 0.41,
 'fruit wholesal': 0.14,
 'real estat agenc': 0.24,
 'event venu': 0.01,
 'frozen dessert supplier': 0.21,
 'wine wholesal import': 0.71,
 'wineri': 0.0,
 'aerospac compani': 0.66,
 'cold storag facil': 0.01,
 'em

In [189]:
calc_pre_rec_at_n(ret_docs_dic, queries_dic, n=-1)[1]

{'home improv store': 0.886,
 'diesel fuel supplier': 0.099,
 'church': 0.04,
 'farm': 1.0,
 'seed supplier': 0.085,
 'account': 0.0,
 'truck compani': 0.14,
 'export': 0.024,
 'grain elev': 0.143,
 'popcorn store': 0.886,
 'agricultur servic': 0.0,
 'warehous': 0.0,
 'agricultur product': 0.0,
 'ranch': 1.0,
 'hold compani': 1.0,
 'farm equip supplier': 0.296,
 'store': 0.818,
 'groceri store': 0.886,
 'rice mill': 0.438,
 'food product supplier': 0.014,
 'account firm': 0.0,
 'produc market': 0.068,
 'pet suppli store': 0.818,
 'wholesal': 0.014,
 'produc wholesal': 0.014,
 'distribut servic': 0.0,
 'crop grower': 1.0,
 'addict treatment center': 0.615,
 'natur good store': 0.545,
 'orchard': 1.0,
 'lumber store': 0.099,
 'mine': 1.0,
 'transport servic': 0.22,
 'invest compani': 1.0,
 'fruit wholesal': 0.197,
 'real estat agenc': 1.0,
 'event venu': 0.023,
 'frozen dessert supplier': 0.288,
 'wine wholesal import': 1.0,
 'wineri': 0.0,
 'aerospac compani': 0.346,
 'cold storag facil

In [191]:
calc_avg_pre(ret_docs_dic, queries_dic, cutoff=-1)[0]

{'home improv store': 0.487,
 'diesel fuel supplier': 0.005,
 'church': 0.024,
 'farm': 0.992,
 'seed supplier': 0.005,
 'account': 0.0,
 'truck compani': 0.021,
 'export': 0.0,
 'grain elev': 0.005,
 'popcorn store': 0.503,
 'agricultur servic': 0.0,
 'warehous': 0.0,
 'agricultur product': 0.0,
 'ranch': 1.0,
 'hold compani': 1.0,
 'farm equip supplier': 0.037,
 'store': 0.522,
 'groceri store': 0.48,
 'rice mill': 0.224,
 'food product supplier': 0.0,
 'account firm': 0.0,
 'produc market': 0.044,
 'pet suppli store': 0.601,
 'wholesal': 0.001,
 'produc wholesal': 0.001,
 'distribut servic': 0.0,
 'crop grower': 0.986,
 'addict treatment center': 0.322,
 'natur good store': 0.203,
 'orchard': 1.0,
 'lumber store': 0.005,
 'mine': 1.0,
 'transport servic': 0.092,
 'invest compani': 1.0,
 'fruit wholesal': 0.025,
 'real estat agenc': 0.998,
 'event venu': 0.002,
 'frozen dessert supplier': 0.192,
 'wine wholesal import': 0.756,
 'wineri': 0.0,
 'aerospac compani': 0.319,
 'cold storag

In [192]:
calc_avg_pre(ret_docs_dic, queries_dic, cutoff=-1)[1]

0.209

In [193]:
calc_NDCG_at_n(ret_docs_dic, queries_dic, n=-1, base=2)

{'home improv store': 0.589,
 'diesel fuel supplier': 0.089,
 'church': 0.157,
 'farm': 0.926,
 'seed supplier': 0.104,
 'account': 0.048,
 'truck compani': 0.185,
 'export': 0.084,
 'grain elev': 0.548,
 'popcorn store': 0.706,
 'agricultur servic': 0.033,
 'warehous': 0.514,
 'agricultur product': 0.033,
 'ranch': 0.9,
 'hold compani': 0.973,
 'farm equip supplier': 0.103,
 'store': 0.655,
 'groceri store': 0.568,
 'rice mill': 0.416,
 'food product supplier': 0.041,
 'account firm': 0.048,
 'produc market': 0.302,
 'pet suppli store': 0.928,
 'wholesal': 0.04,
 'produc wholesal': 0.031,
 'distribut servic': 0.049,
 'crop grower': 0.929,
 'addict treatment center': 0.555,
 'natur good store': 0.399,
 'orchard': 0.899,
 'lumber store': 0.113,
 'mine': 0.96,
 'transport servic': 0.326,
 'invest compani': 0.918,
 'fruit wholesal': 0.213,
 'real estat agenc': 0.924,
 'event venu': 0.089,
 'frozen dessert supplier': 0.503,
 'wine wholesal import': 0.736,
 'wineri': 0.027,
 'aerospac compa